In [10]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
%load_ext blackcellmagic

The blackcellmagic extension is already loaded. To reload it, use:
  %reload_ext blackcellmagic


In [12]:
import numpy as np
import math
import pickle as pkl
from scipy.special import comb

from pyphi import visualize as viz
from pyphi import relations as rel

import matplotlib.pyplot as plt
import string

import random
import imageio

# Chapter 3 system

In [13]:
with open(r"ch3_ces.pkl", "rb") as f:
    ces = pkl.load(f)
    
with open(r"ch3_rels.pkl", "rb") as f:
    rels = pkl.load(f)
    
with open(r"ch3_subsystem.pkl", "rb") as f:
    system = pkl.load(f)

In [14]:
from pyphi import simulate_ces as sim

In [7]:
path = sim.spring_force_simulation(
    ces,
    rels,
    distinction_relation_force_balance=1,
    friction_factor=5,
    repulsion_factor=1,
    spring_factor=1,
    T=100,
    delta=0.01,
    mass=None,
    immovable=(),
    initial_positions="singularity",
    return_path=False,
    adjust_force_by_phi=True,
)

In [27]:
f = sim.plot_simulated_ces(
    system,
    ces,
    rels,
    simulation_kwargs={
        "T": 300,
        "distinction_relation_force_balance": 5,
        "initial_positions": "mechanisms outside",
        "immovable": range(len(ces)),
    },
    plotting_kwargs={
        "save_plot_to_html": False,
        "png_name": "pngs/ch3.png",
        "eye_coordinates": (0, 0, 1),
        "plot_dimensions": [1000, 1200],
        "autosize": False,
    },
)

Running physics simulation on the components of the CES
Plotting the CES


In [16]:
sim.get_ces_gif(
    'pngs/func/',
    system,
    ces,
    rels,
    time_grain=5,
    plot_final=True,
    plotting_kwargs=dict(),
)

Running physics simulation on the components of the CES
Creating the gif



Plotting the final CES


# 8 node space

In [28]:
with open(r"space_ces_with_nodelabels.pkl", "rb") as f:
    ces = pkl.load(f)
    
with open(r"space_2relations.pkl", "rb") as f:
    rels = pkl.load(f)
    
with open(r"space_subsystem.pkl", "rb") as f:
    system = pkl.load(f)

In [29]:
path = sim.spring_force_simulation(
    ces,
    rels,
    distinction_relation_force_balance=1,
    friction_factor=5,
    repulsion_factor=1,
    spring_factor=1,
    T=10,
    delta=0.01,
    mass=None,
    immovable=(),
    initial_positions="singularity",
    return_path=False,
    adjust_force_by_phi=True,
)

In [39]:
import math
def find_continuous_members(members):
    continuous_members = [m for m in members
        if m==tuple(range(m[0],m[0]+len(m)))
    ]
    return continuous_members

def circlepoints(r,n):
    return [(math.cos(2*math.pi/n*x)*r,math.sin(2*math.pi/n*x)*r) for x in range(0,n)]

def divide_mechs_by_order(mechs):
    top_order = max([len(m) for m in mechs])
    return [[m for m in mechs if len(m)==o] for o in range(1,top_order+1)]

def make_continuous_mech_cone(mechs,radii=None,layer_height=1):
    continuous_mechs = find_continuous_members(mechs)
    mechs_by_order = divide_mechs_by_order(continuous_mechs)
    orders_n = len(mechs_by_order)
    if radii is None:
        radii = [len(order)-1 for order in mechs_by_order]
    coords = []
    zs = range(0,orders_n*layer_height,layer_height)
    for o,order in enumerate(mechs_by_order):
        positions = circlepoints(len(order)-1,len(order))
        order_coords = np.array([[position[0],position[1],zs[o]] for position in positions])
        coords.append(order_coords)
        
    return coords

In [40]:
mechs = [c.mechanism for c in ces]
continuous_mechs = find_continuous_members(mechs)
coords = make_continuous_mech_cone(mechs, layer_height=2)


In [42]:
array_coords = np.concatenate(coords)

In [64]:
indices = []
for m in continuous_mechs:
    for i,c in enumerate(ces):
        if c.mechanism == m:
            indices.append(i)
all_indices = indices + list(np.array([[len(ces)+2*i, len(ces)+2*i+1] for i in indices]).flatten())
            
mech_coords = []
for c in ces:
    if c.mechanism in continuous_mechs:
        for m,mech in enumerate(continuous_mechs):
            if c.mechanism==mech:
                mech_coords.append(list(array_coords[m]))
    else:
        mech_coords.append(list(np.array([0,0,0])))

init = np.array([m for m in mech_coords])

purviews = np.repeat(init, repeats=2, axis=0)

initial_postitions = np.append(init,purviews,axis=0)

In [65]:
path = sim.spring_force_simulation(
    ces,
    rels,
    distinction_relation_force_balance=100,
    friction_factor=5,
    repulsion_factor=0.01,
    spring_factor=1,
    T=10,
    delta=0.01,
    mass=None,
    immovable=tuple(indices),
    initial_positions=initial_postitions.transpose(),
    return_path=True,
    adjust_force_by_phi=True,
)

/home/bjuel/projects/pyphiviz/pyphi/pyphi/simulate_ces.py:303: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison

/home/bjuel/projects/pyphiviz/pyphi/pyphi/simulate_ces.py:308: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison

/home/bjuel/projects/pyphiviz/pyphi/pyphi/simulate_ces.py:313: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison

/home/bjuel/projects/pyphiviz/pyphi/pyphi/simulate_ces.py:318: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



In [ ]:
import random

sim.plot_simulated_ces(
    system,
    ces,
    random.sample(rels,10000),
    simulation_kwargs={
        "T": 10,
        "distinction_relation_force_balance": 1,
        'immovable':tuple(all_indices),
        'initial_positions':initial_postitions.transpose(),
    },
    plotting_kwargs={
        "network_name": "8node_space",
        "eye_coordinates": (0, 1, 0),
        "plot_dimensions": [1000, 1200],
        "autosize": False,
    },
)